In [1]:
from datetime import datetime
from pathlib import Path
from dotenv import load_dotenv
import os
import os
import sys
import pandas as pd
pd.options.mode.chained_assignment = None
from pandas import json_normalize
from datetime import datetime
from pathlib import Path
import requests
from requests.exceptions import ConnectionError
import json
import time
import xmltodict
from zipfile import ZipFile
import shapely
import shapely.wkt
from shapely.ops import transform
import pyproj
import shutil
import numpy as np
os.environ['PROJ_NETWORK'] = 'OFF'

In [2]:
pd.set_option('display.max_rows', 1900)
pd.set_option('display.max_columns', 100)

In [3]:
start_time = datetime.utcnow()

# USER MUST EDIT THE ENVIRONMENT FILE REFERENCED BELOW, OR CREATE THEIR OWN FILE AND REFERENCE IT
load_dotenv('PRE.env')

# set configuration based on contents of the ENVIRONMENT FILE.
conn = {
    'domain': os.getenv("HOST"),
    'username': os.getenv("API_USER"),
    'access_token': os.getenv("API_TOKEN"),
}

# use default path to local "output" directory
#output_dir = eodslib.make_output_dir(Path.cwd() / 'output')

# specify a particular ARD to download using 'title' keyword
eods_params = {
    #'output_dir':output_dir,
    #'title':'S2B_20200424_lat55lon215_T30UWF_ORB037_utm30n_osgb_vmsk_sharp_rad_srefdem_stdsref',
    'find_least_cloud': True,
    'sat_id': 2
    }

kwargs = eods_params

# list_of_layers, df = query_catalog(conn, **eods_params)

In [4]:
params = {
        'username':conn['username'],
        'api_key':conn['access_token'],
        'offset':0,
    }

# set output path if not specified
if 'output_dir' not in kwargs:
    kwargs['output_dir']=Path.cwd()

# set limit to a sufficiently big number if not specified
if 'limit' not in kwargs:
    params.update({'limit':20000})
else:
    params.update({'limit':kwargs['limit']})

# set type to layer if "raster" or "vector" not specified
if 'type' not in kwargs:
    kwargs['type']='layer'
else:
    params.update({'type__in':kwargs['type']})

if 'verify' not in kwargs:
    kwargs['verify'] = True

if 'sat_id' in kwargs and 'find_least_cloud' in kwargs:
    if kwargs['sat_id'] == 1:            
        # throw an error if user specifies an s2 custom function with s1
        raise ValueError("QUERY failed, you have specified 'sat_id'=1 and 'find_least_cloud'=True. Use 'sat_id'=2 and 'find_least_cloud'=True")

if 'sat_id' in kwargs:
    params.update({'keywords__slug__in': 'sentinel-' + str(kwargs['sat_id'])})        

# date filter condition check and set
if 'start_date' in kwargs and 'end_date' not in kwargs:
    raise ValueError("QUERY failed, if querying by date, please specify *BOTH* 'start_date' and 'end_date'")
elif 'start_date' not in kwargs and 'end_date' in kwargs:
    raise ValueError("QUERY failed, if querying by date, please specify *BOTH* 'start_date' and 'end_date'")
elif 'start_date' in kwargs and 'end_date' in kwargs:
    params.update({'date__range': kwargs['start_date'] + ' 00:00,' + kwargs['end_date'] + ' 00:00'})

if 'title' in kwargs:
    params.update({'q': kwargs['title']})

if 'geom' in kwargs:
    params.update({'geometry': kwargs['geom']})

# cloud filter condition check and set    
if 'cloud_min' in kwargs and 'cloud_max' not in kwargs:
    raise ValueError("QUERY failed, if querying by cloud cover, please specify *BOTH* 'cloud_min' and 'cloud_max'")
elif 'cloud_min' not in kwargs and 'cloud_max' in kwargs:
    raise ValueError("QUERY failed, if querying by cloud cover, please specify *BOTH* 'cloud_min' and 'cloud_max'")
elif 'cloud_min' in kwargs and 'cloud_max' in kwargs:
    if kwargs['sat_id'] == 1:
        raise ValueError("QUERY failed, if querying by cloud cover, please specify 'sat_id'=2")
    elif kwargs['sat_id'] == 2:
        params.update({'cc_min': kwargs['cloud_min']})
        params.update({'cc_max': kwargs['cloud_max']})            

print('\n' + datetime.utcnow().isoformat() + ' :: PARAMENTERS USED = ' + str(params))


2021-08-10T14:53:53.508848 :: PARAMENTERS USED = {'username': 'admin', 'api_key': 'ndA91y6TWFBFeqjEGMhkgdBTJXLnsL', 'offset': 0, 'limit': 20000, 'keywords__slug__in': 'sentinel-2'}


In [5]:
response = requests.get(
    conn['domain'] + '/api/base/search',
    params=params,
    verify=kwargs['verify'],
    headers={'User-Agent': 'python'}
)

if response.status_code == 200:

    print(datetime.utcnow().isoformat() + ' :: RESPONSE STATUS = 200 (SUCCESS)')
    print(datetime.utcnow().isoformat() + ' :: QUERY URL USED = ' + response.url)

    # create a json object of the api payload content
    json_response = json.loads(response.content)

    if json_response['meta']['total_count'] > 0:

        df = json_normalize(json_response, 'objects')

        # add extra cols to df for s2 info
        if 'sat_id' in kwargs:
            if kwargs['sat_id'] == 2:
                df['granule-ref'] = df['title'].str.split('_',n=4).str[3]
                df['orbit-ref'] = df['title'].str.split('_',n=5).str[-2]
                df['ARCSI_CLOUD_COVER'] =df['supplemental_information'].str.split(n=6).str[5]           

2021-08-10T14:53:59.049514 :: RESPONSE STATUS = 200 (SUCCESS)
2021-08-10T14:53:59.049639 :: QUERY URL USED = https://eob-pre1.azure.defra.cloud/api/base/search/?username=admin&api_key=ndA91y6TWFBFeqjEGMhkgdBTJXLnsL&offset=0&limit=20000&keywords__slug__in=sentinel-2


In [6]:
df

abstract  \
0     These data have been created by the Department...   
1     These data have been created by the Department...   
2     These data have been created by the Department...   
3     These data have been created by the Department...   
4     These data have been created by the Department...   
5     These data have been created by the Department...   
6     These data have been created by the Department...   
7     These data have been created by the Department...   
8     These data have been created by the Department...   
9     These data have been created by the Department...   
10    These data have been created by the Department...   
11    These data have been created by the Department...   
12    These data have been created by the Department...   
13    These data have been created by the Department...   
14    These data have been created by the Department...   
15    These data have been created by the Department...   
16    These data have been created by the Department...   
17    These data have been created by the Department...   
18    These data have been created by the Department...   
19    These data have been created by the Department...   
20    These data have been created by the Department...   
21    These data have been created by the Department...   
22    These data have been created by the Department...   
23    These data have been created by the Department...   
24    These data have been created by the Department...   
25    These data have been created by the Department...   
26    These data have been created by the Department...   
27    These data have been created by the Department...   
28    These data have been created by the Department...   
29    These data have been created by the Department...   
30    These data have been created by the Department...   
31    These data have been created by the Department...   
32    These data have been created by the Department...   
33    These data have been created by the Department...   
34    These data have been created by the Department...   
35    These data have been created by the Department...   
36    These data have been created by the Department...   
37    These data have been created by the Department...   
38    These data have been created by the Department...   
39    These data have been created by the Department...   
40    These data have been created by the Department...   
41    These data have been created by the Department...   
42    These data have been created by the Department...   
43    These data have been created by the Department...   
44    These data have been created by the Department...   
45    These data have been created by the Department...   
46    These data have been created by the Department...   
47    These data have been created by the Department...   
48    These data have been created by the Department...   
49    These data have been created by the Department...   
50    These data have been created by the Department...   
51    These data have been created by the Department...   
52    These data have been created by the Department...   
53    These data have been created by the Department...   
54    These data have been created by the Department...   
55    These data have been created by the Department...   
56    These data have been created by the Department...   
57    These data have been created by the Department...   
58    These data have been created by the Department...   
59    These data have been created by the Department...   
60    These data have been created by the Department...   
61    These data have been created by the Department...   
62    These data have been created by the Department...   
63    These data have been created by the Department...   
64    These data have been created by the Department...   
65    These data have been created by the Department...   
66    These data have been created by the Department...   
67    These data have been created 

In [7]:
df['title'].str.split('_', n=4)[4]

['S2A',
 '20210809',
 'lat51lon062',
 'T30UYB',
 'ORB137_utm30n_osgb_vmsk_sharp_rad_srefdem_stdsref']

In [8]:
if len(df[df['title'].str.contains('SPLIT')]) > 0:

    print(datetime.utcnow().isoformat() + ' :: INFO. Split Granules found in query results ... removing')

    # create a title substring which can be matched against a split list
    df['title_stub'] = df['title'].str.split('_T', expand=True).loc[:,0] + '_' + df['granule-ref'].str[:6]

    """# create a Series object for that only contains the title 'sub string' 
    s = df[df["title"].str.contains("SPLIT")].title.str.split('SPLIT1',expand=True).loc[:,0]

    # select rows from main dataframe where records DO NOT MATCH (~ = syntax) the 'split' series of title stub strings
    filtered_out_split = df[~df.title_stub.isin(s)]"""

2021-08-10T14:53:59.955933 :: INFO. Split Granules found in query results ... removing


In [9]:
temp_df = df[df['split_granule.name'].notna()][['alternate', 'ARCSI_CLOUD_COVER']].copy()

In [10]:
temp_df

alternate    ARCSI_CLOUD_COVER
445   geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...    0.173685684800148
446   geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...  0.20804637670516968
450   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...  0.14184147119522095
453   geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...  0.07855145633220673
649   geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...   0.9106923341751099
653   geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...   0.6540082693099976
658   geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...   0.7374271154403687
664   geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...   0.6250476241111755
670   geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...   0.7653273344039917
671   geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...  0.30046480894088745
677   geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...   0.6763184666633606
681   geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...   0.7163509130477905
685   geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...   0.5079259872436523
689   geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...   0.5655169486999512
747   geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...  0.14500795304775238
758   geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...    0.451851487159729
1026  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...   0.7955636978149414
1039  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...   0.8122555613517761
1040  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...   0.6726863980293274
1041  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...   0.9149492979049683
1045  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...   0.8316067457199097
1046  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...   0.9127920866012573

In [11]:
temp_df.rename(columns={"alternate": "split_granule.name", "ARCSI_CLOUD_COVER": "split_ARCSI_CLOUD_COVER"}, inplace=True)

In [12]:
temp_df

split_granule.name  \
445   geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...   
446   geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...   
450   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
453   geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...   
649   geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...   
653   geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...   
658   geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...   
664   geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...   
670   geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...   
671   geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...   
677   geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...   
681   geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...   
685   geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...   
689   geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...   
747   geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...   
758   geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...   
1026  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...   
1039  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...   
1040  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...   
1041  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...   
1045  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...   
1046  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...   

     split_ARCSI_CLOUD_COVER  
445        0.173685684800148  
446      0.20804637670516968  
450      0.14184147119522095  
453      0.07855145633220673  
649       0.9106923341751099  
653       0.6540082693099976  
658       0.7374271154403687  
664       0.6250476241111755  
670       0.7653273344039917  
671      0.30046480894088745  
677       0.6763184666633606  
681       0.7163509130477905  
685       0.5079259872436523  
689       0.5655169486999512  
747      0.14500795304775238  
758        0.451851487159729  
1026      0.7955636978149414  
1039      0.8122555613517761  
1040      0.6726863980293274  
1041      0.9149492979049683  
1045      0.8316067457199097  
1046      0.9127920866012573

In [13]:
merged_df = df[df['split_granule.name'].notna()].reset_index().merge(temp_df, how='outer', on='split_granule.name').set_index('index')

In [ ]:
merged_df

In [14]:
df[df['split_granule.name'].notna()]

abstract  \
445   These data have been created by the Department...   
446   These data have been created by the Department...   
450   These data have been created by the Department...   
453   These data have been created by the Department...   
649   These data have been created by the Department...   
653   These data have been created by the Department...   
658   These data have been created by the Department...   
664   These data have been created by the Department...   
670   These data have been created by the Department...   
671   These data have been created by the Department...   
677   These data have been created by the Department...   
681   These data have been created by the Department...   
685   These data have been created by the Department...   
689   These data have been created by the Department...   
747   These data have been created by the Department...   
758   These data have been created by the Department...   
1026  These data have been created by the Department...   
1039  These data have been created by the Department...   
1040  These data have been created by the Department...   
1041  These data have been created by the Department...   
1045  These data have been created by the Department...   
1046  These data have been created by the Department...   

                                              alternate  \
445   geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...   
446   geonode:S2A_20200810_lat50lon503_T30UUA_ORB080...   
450   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
453   geonode:S2A_20200810_lat50lon503_T30UUASPLIT1_...   
649   geonode:S2A_20200728_lat55lon213_T30UWG_ORB037...   
653   geonode:S2A_20200728_lat55lon213_T30UWGSPLIT1_...   
658   geonode:S2A_20200728_lat55lon061_T30UXF_ORB037...   
664   geonode:S2A_20200728_lat55lon215_T30UWFSPLIT1_...   
670   geonode:S2A_20200728_lat55lon215_T30UWF_ORB037...   
671   geonode:S2A_20200728_lat55lon061_T30UXFSPLIT1_...   
677   geonode:S2B_20200727_lat52lon07_T30UYC_ORB094_...   
681   geonode:S2B_20200727_lat52lon089_T31UCT_ORB094...   
685   geonode:S2B_20200727_lat52lon07_T30UYCSPLIT1_O...   
689   geonode:S2B_20200727_lat52lon089_T31UCTSPLIT1S...   
747   geonode:S2A_20200721_lat51lon364_T30UVB_ORB080...   
758   geonode:S2A_20200721_lat51lon364_T30UVBSPLIT1_...   
1026  geonode:S2A_20200628_lat55lon215_T30UWFSPLIT1_...   
1039  geonode:S2A_20200628_lat54lon066_T30UXE_ORB037...   
1040  geonode:S2A_20200628_lat55lon215_T30UWF_ORB037...   
1041  geonode:S2A_20200628_lat55lon061_T30UXF_ORB037...   
1045  geonode:S2A_20200628_lat54lon066_T30UXESPLIT1_...   
1046  geonode:S2A_20200628_lat55lon061_T30UXFSPLIT1_...   

                       category   category__gn_description  cloud_cover  \
445   imagerybasemapsearthcover  imagerybasemapsearthcover         17.0   
446   imagerybasemapsearthcover  imagerybasemapsearthcover         21.0   
450   imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   
453   imagerybasemapsearthcover  imagerybasemapsearthcover          8.0   
649   imagerybasemapsearthcover  imagerybasemapsearthcover         91.0   
653   imagerybasemapsearthcover  imagerybasemapsearthcover         65.0   
658   imagerybasemapsearthcover  imagerybasemapsearthcover         74.0   
664   imagerybasemapsearthcover  imagerybasemapsearthcover         63.0   
670   imagerybasemapsearthcover  imagerybasemapsearthcover         77.0   
671   imagerybasemapsearthcover  imagerybasemapsearthcover         30.0   
677   imagerybasemapsearthcover  imagerybasemapsearthcover         68.0   
681   imagerybasemapsearthcover  imagerybasemapsearthcover         72.0   
685   imagerybasemapsearthcover  imagerybasemapsearthcover         51.0   
689   imagerybasemapsearthcover  imagerybasemapsearthcover         57.0   
747   imagerybasemapsearthcover  imagerybasemapsearthcover         15.0   
758   imagerybasemapsearthcover  imagerybasemapsearthcover         45.0   
1026  imagerybasemapsearthcover  imagerybasemapsearthcov

In [15]:
df['split_ARCSI_CLOUD_COVER'] = np.nan

In [16]:
df.loc[df['split_granule.name'].notna(), 'split_ARCSI_CLOUD_COVER'] = merged_df['split_ARCSI_CLOUD_COVER']

In [17]:
df

abstract  \
0     These data have been created by the Department...   
1     These data have been created by the Department...   
2     These data have been created by the Department...   
3     These data have been created by the Department...   
4     These data have been created by the Department...   
5     These data have been created by the Department...   
6     These data have been created by the Department...   
7     These data have been created by the Department...   
8     These data have been created by the Department...   
9     These data have been created by the Department...   
10    These data have been created by the Department...   
11    These data have been created by the Department...   
12    These data have been created by the Department...   
13    These data have been created by the Department...   
14    These data have been created by the Department...   
15    These data have been created by the Department...   
16    These data have been created by the Department...   
17    These data have been created by the Department...   
18    These data have been created by the Department...   
19    These data have been created by the Department...   
20    These data have been created by the Department...   
21    These data have been created by the Department...   
22    These data have been created by the Department...   
23    These data have been created by the Department...   
24    These data have been created by the Department...   
25    These data have been created by the Department...   
26    These data have been created by the Department...   
27    These data have been created by the Department...   
28    These data have been created by the Department...   
29    These data have been created by the Department...   
30    These data have been created by the Department...   
31    These data have been created by the Department...   
32    These data have been created by the Department...   
33    These data have been created by the Department...   
34    These data have been created by the Department...   
35    These data have been created by the Department...   
36    These data have been created by the Department...   
37    These data have been created by the Department...   
38    These data have been created by the Department...   
39    These data have been created by the Department...   
40    These data have been created by the Department...   
41    These data have been created by the Department...   
42    These data have been created by the Department...   
43    These data have been created by the Department...   
44    These data have been created by the Department...   
45    These data have been created by the Department...   
46    These data have been created by the Department...   
47    These data have been created by the Department...   
48    These data have been created by the Department...   
49    These data have been created by the Department...   
50    These data have been created by the Department...   
51    These data have been created by the Department...   
52    These data have been created by the Department...   
53    These data have been created by the Department...   
54    These data have been created by the Department...   
55    These data have been created by the Department...   
56    These data have been created by the Department...   
57    These data have been created by the Department...   
58    These data have been created by the Department...   
59    These data have been created by the Department...   
60    These data have been created by the Department...   
61    These data have been created by the Department...   
62    These data have been created by the Department...   
63    These data have been created by the Department...   
64    These data have been created by the Department...   
65    These data have been created by the Department...   
66    These data have been created by the Department...   
67    These data have been created 

In [18]:
df.loc[df['id']==9281, 'ARCSI_CLOUD_COVER'] = '0.2'
df.loc[df['id']==9117, 'ARCSI_CLOUD_COVER'] = '0.2'

In [19]:
split_cloud_cover = np.where(df['split_granule.name'].notna(), ((df['ARCSI_CLOUD_COVER'].astype(
    float) + df['split_ARCSI_CLOUD_COVER'].astype(
    float))/2).astype(str), df['ARCSI_CLOUD_COVER'])

df['split_cloud_cover'] = split_cloud_cover

In [20]:
df

abstract  \
0     These data have been created by the Department...   
1     These data have been created by the Department...   
2     These data have been created by the Department...   
3     These data have been created by the Department...   
4     These data have been created by the Department...   
5     These data have been created by the Department...   
6     These data have been created by the Department...   
7     These data have been created by the Department...   
8     These data have been created by the Department...   
9     These data have been created by the Department...   
10    These data have been created by the Department...   
11    These data have been created by the Department...   
12    These data have been created by the Department...   
13    These data have been created by the Department...   
14    These data have been created by the Department...   
15    These data have been created by the Department...   
16    These data have been created by the Department...   
17    These data have been created by the Department...   
18    These data have been created by the Department...   
19    These data have been created by the Department...   
20    These data have been created by the Department...   
21    These data have been created by the Department...   
22    These data have been created by the Department...   
23    These data have been created by the Department...   
24    These data have been created by the Department...   
25    These data have been created by the Department...   
26    These data have been created by the Department...   
27    These data have been created by the Department...   
28    These data have been created by the Department...   
29    These data have been created by the Department...   
30    These data have been created by the Department...   
31    These data have been created by the Department...   
32    These data have been created by the Department...   
33    These data have been created by the Department...   
34    These data have been created by the Department...   
35    These data have been created by the Department...   
36    These data have been created by the Department...   
37    These data have been created by the Department...   
38    These data have been created by the Department...   
39    These data have been created by the Department...   
40    These data have been created by the Department...   
41    These data have been created by the Department...   
42    These data have been created by the Department...   
43    These data have been created by the Department...   
44    These data have been created by the Department...   
45    These data have been created by the Department...   
46    These data have been created by the Department...   
47    These data have been created by the Department...   
48    These data have been created by the Department...   
49    These data have been created by the Department...   
50    These data have been created by the Department...   
51    These data have been created by the Department...   
52    These data have been created by the Department...   
53    These data have been created by the Department...   
54    These data have been created by the Department...   
55    These data have been created by the Department...   
56    These data have been created by the Department...   
57    These data have been created by the Department...   
58    These data have been created by the Department...   
59    These data have been created by the Department...   
60    These data have been created by the Department...   
61    These data have been created by the Department...   
62    These data have been created by the Department...   
63    These data have been created by the Department...   
64    These data have been created by the Department...   
65    These data have been created by the Department...   
66    These data have been created by the Department...   
67    These data have been created 

In [21]:
no_split_df = df[~df['title'].str.contains("SPLIT")]

In [22]:
no_split_df[no_split_df['granule-ref'] == 'T29UQR']

abstract  \
38    These data have been created by the Department...   
63    These data have been created by the Department...   
106   These data have been created by the Department...   
145   These data have been created by the Department...   
188   These data have been created by the Department...   
211   These data have been created by the Department...   
275   These data have been created by the Department...   
327   These data have been created by the Department...   
372   These data have been created by the Department...   
401   These data have been created by the Department...   
450   These data have been created by the Department...   
504   These data have been created by the Department...   
534   These data have been created by the Department...   
563   These data have been created by the Department...   
647   These data have been created by the Department...   
752   These data have been created by the Department...   
821   These data have been created by the Department...   
841   These data have been created by the Department...   
870   These data have been created by the Department...   
941   These data have been created by the Department...   
1008  These data have been created by the Department...   
1022  These data have been created by the Department...   

                                              alternate  \
38    geonode:S2B_20210807_lat50lon544_T29UQR_ORB037...   
63    geonode:S2A_20210805_lat50lon544_T29UQR_ORB080...   
106   geonode:S2A_20210802_lat50lon544_T29UQR_ORB037...   
145   geonode:S2B_20210731_lat50lon544_T29UQR_ORB080...   
188   geonode:S2B_20210728_lat50lon544_T29UQR_ORB037...   
211   geonode:S2A_20210726_lat50lon544_T29UQR_ORB080...   
275   geonode:S2B_20210721_lat50lon544_T29UQR_ORB080...   
327   geonode:S2B_20210718_lat50lon544_T29UQR_ORB037...   
372   geonode:S2B_20201004_lat50lon544_T29UQR_ORB080...   
401   geonode:S2B_20200914_lat50lon544_T29UQR_ORB080...   
450   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
504   geonode:S2A_20200807_lat50lon544_T29UQR_ORB037...   
534   geonode:S2B_20200805_lat50lon544_T29UQR_ORB080...   
563   geonode:S2B_20200802_lat50lon544_T29UQR_ORB037...   
647   geonode:S2A_20200728_lat50lon544_T29UQR_ORB037...   
752   geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   
821   geonode:S2B_20200716_lat50lon544_T29UQR_ORB080...   
841   geonode:S2B_20200713_lat50lon544_T29UQR_ORB037...   
870   geonode:S2A_20200711_lat50lon544_T29UQR_ORB080...   
941   geonode:S2B_20200706_lat50lon544_T29UQR_ORB080...   
1008  geonode:S2A_20200701_lat50lon544_T29UQR_ORB080...   
1022  geonode:S2A_20200628_lat50lon544_T29UQR_ORB037...   

                       category   category__gn_description  cloud_cover  \
38    imagerybasemapsearthcover  imagerybasemapsearthcover         66.0   
63    imagerybasemapsearthcover  imagerybasemapsearthcover         18.0   
106   imagerybasemapsearthcover  imagerybasemapsearthcover         90.0   
145   imagerybasemapsearthcover  imagerybasemapsearthcover         35.0   
188   imagerybasemapsearthcover  imagerybasemapsearthcover         77.0   
211   imagerybasemapsearthcover  imagerybasemapsearthcover         90.0   
275   imagerybasemapsearthcover  imagerybasemapsearthcover         21.0   
327   imagerybasemapsearthcover  imagerybasemapsearthcover          3.0   
372   imagerybasemapsearthcover  imagerybasemapsearthcover         92.0   
401   imagerybasemapsearthcover  imagerybasemapsearthcover         46.0   
450   imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   
504   imagerybasemapsearthcover  imagerybasemapsearthcover         59.0   
534   imagerybasemapsearthcover  imagerybasemapsearthcover         50.0   
563   imagerybasemapsearthcover  imagerybasemapsearthcover         80.0   
647   imagerybasemapsearthcover  imagerybasemapsearthcover         42.0   
752   imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   
821   imagerybasemapsearthcover  imagerybasemapsearthcov

In [23]:
# import safe granule-orb list
if Path(Path.cwd() / 'static' / 'safe-granule-orbit-list.txt').exists():
    df_safe_list = pd.read_csv(Path.cwd() / 'static' / 'safe-granule-orbit-list.txt')
else:
    raise ValueError('ERROR :: safe-granule-orbit-list.txt cannot be found')

# create new col that matches the granule-orbit syntax
no_split_df['gran-orb'] = no_split_df['granule-ref'].str[:6] + '_' + no_split_df['orbit-ref']
no_split_df['granule-stub'] = no_split_df['granule-ref'].str[:6]

df['gran-orb'] = df['granule-ref'].str[:6] + '_' + df['orbit-ref']
df['granule-stub'] = df['granule-ref'].str[:6]

filtered_df = pd.merge(no_split_df,df_safe_list)

"""split_cloud_cover = np.where(filtered_df['split_granule.name'].notna(), ((filtered_df['ARCSI_CLOUD_COVER'].astype(
    float) + df[df['title'] == filtered_df['split_granule.name']]['split_granule.cloud_cover'].astype(float))/2).astype(str), filtered_df['ARCSI_CLOUD_COVER'])

filtered_df['split_cloud_cover'] = split_cloud_cover"""

if len(filtered_df) > 0:
    return_df = filtered_df.sort_values("split_cloud_cover").groupby(["granule-stub"], as_index=False).nth(0).sort_values("granule-stub")

    matching_split_series = return_df[return_df['split_granule.name'].notna()]['split_granule.name']
    matching_split_df = df[df['alternate'].isin(matching_split_series)]

    # matching_split_df['split_cloud_cover'] = ((matching_split_df['ARCSI_CLOUD_COVER'].astype(float) + matching_split_df['split_granule.cloud_cover'].astype(float))/2).astype(str)

    return_df = pd.concat([return_df, matching_split_df], ignore_index=True)
    
else:
    raise ValueError('ERROR : You have selected find_lowest_cloud=True BUT your search criteria is too narrow, spatially or temporally and did not match any granule references in "./static/safe-granule-orbit-list.txt". Suggest widening your search')


In [24]:
df[df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
752  These data have been created by the Department...   

                                             alternate  \
752  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
752  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

    csw_type                                   csw_wkt_geometry  \
752  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
752  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

       id                                           keywords  \
752  9281  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
752  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
752              0       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
752            NaN  EPSG:27700  raster   

                              supplemental_information  \
752  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
752  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
752  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
752  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

    split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
752                NaN      T29UQR    ORB080               0.2   

                          title_stub split_ARCSI_CLOUD_COVER  \
752  S2A_20200721_lat50lon544_T29UQR                     NaN   

    split_cloud_cover       gran-orb granule-stub  
752               0.2  T29UQR_ORB080       T29UQR

In [25]:
df[df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
450  These data have been created by the Department...   

                                             alternate  \
450  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
450  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

    csw_type                                   csw_wkt_geometry  \
450  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
450  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

       id                                           keywords  \
450  9746  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
450  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
450              2       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
450            NaN  EPSG:27700  raster   

                              supplemental_information  \
450  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
450  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
450  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
450  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                    split_granule.name granule-ref orbit-ref  \
450  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

       ARCSI_CLOUD_COVER                       title_stub  \
450  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

    split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
450       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [26]:
no_split_df[no_split_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
752  These data have been created by the Department...   

                                             alternate  \
752  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
752  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

    csw_type                                   csw_wkt_geometry  \
752  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
752  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

       id                                           keywords  \
752  9281  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
752  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
752              0       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
752            NaN  EPSG:27700  raster   

                              supplemental_information  \
752  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
752  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
752  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
752  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

    split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
752                NaN      T29UQR    ORB080               0.2   

                          title_stub split_ARCSI_CLOUD_COVER  \
752  S2A_20200721_lat50lon544_T29UQR                     NaN   

    split_cloud_cover       gran-orb granule-stub  
752               0.2  T29UQR_ORB080       T29UQR

In [27]:
no_split_df[no_split_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
450  These data have been created by the Department...   

                                             alternate  \
450  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
450  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

    csw_type                                   csw_wkt_geometry  \
450  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
450  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

       id                                           keywords  \
450  9746  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
450  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
450              2       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
450            NaN  EPSG:27700  raster   

                              supplemental_information  \
450  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
450  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
450  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
450  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                    split_granule.name granule-ref orbit-ref  \
450  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

       ARCSI_CLOUD_COVER                       title_stub  \
450  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

    split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
450       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [28]:
filtered_df[filtered_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
386  These data have been created by the Department...   

                                             alternate  \
386  geonode:S2A_20200721_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
386  imagerybasemapsearthcover  imagerybasemapsearthcover          9.0   

    csw_type                                   csw_wkt_geometry  \
386  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
386  2020-07-21T11:33:21  /layers/geonode:S2A_20200721_lat50lon544_T29UQ...   

       id                                           keywords  \
386  9281  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
386  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
386              0       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
386            NaN  EPSG:27700  raster   

                              supplemental_information  \
386  Data Collection Time: 11:33:21\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
386  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
386  S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
386  48f3bf5a-c468-421e-9ba6-124985e43ed3                        NaN   

    split_granule.name granule-ref orbit-ref ARCSI_CLOUD_COVER  \
386                NaN      T29UQR    ORB080               0.2   

                          title_stub split_ARCSI_CLOUD_COVER  \
386  S2A_20200721_lat50lon544_T29UQR                     NaN   

    split_cloud_cover       gran-orb granule-stub  
386               0.2  T29UQR_ORB080       T29UQR

In [29]:
filtered_df[filtered_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
384  These data have been created by the Department...   

                                             alternate  \
384  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                      category   category__gn_description  cloud_cover  \
384  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0   

    csw_type                                   csw_wkt_geometry  \
384  dataset  POLYGON((-6.17931146696 49.4453444507,-6.17931...   

                    date                                         detail_url  \
384  2020-08-10T11:33:31  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...   

       id                                           keywords  \
384  9746  [analysis-ready-data, earth-observation, satel...   

                                              location owner__username  \
384  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

     popular_count  rating                   regions  share_count  \
384              2       0  [Europe, United Kingdom]            0   

     split_granule        srid subtype  \
384            NaN  EPSG:27700  raster   

                              supplemental_information  \
384  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                         thumbnail_url  \
384  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                                 title   type  \
384  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                     uuid  split_granule.cloud_cover  \
384  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                    split_granule.name granule-ref orbit-ref  \
384  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

       ARCSI_CLOUD_COVER                       title_stub  \
384  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

    split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
384       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [30]:
return_df[return_df['title'] == 'S2A_20200721_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

Empty DataFrame
Columns: [abstract, alternate, category, category__gn_description, cloud_cover, csw_type, csw_wkt_geometry, date, detail_url, id, keywords, location, owner__username, popular_count, rating, regions, share_count, split_granule, srid, subtype, supplemental_information, thumbnail_url, title, type, uuid, split_granule.cloud_cover, split_granule.name, granule-ref, orbit-ref, ARCSI_CLOUD_COVER, title_stub, split_ARCSI_CLOUD_COVER, split_cloud_cover, gran-orb, granule-stub]
Index: []

In [31]:
return_df[return_df['title'] == 'S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_osgb_vmsk_sharp_rad_srefdem_stdsref']

abstract  \
1  These data have been created by the Department...   

                                           alternate  \
1  geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   

                    category   category__gn_description  cloud_cover csw_type  \
1  imagerybasemapsearthcover  imagerybasemapsearthcover         14.0  dataset   

                                    csw_wkt_geometry                 date  \
1  POLYGON((-6.17931146696 49.4453444507,-6.17931...  2020-08-10T11:33:31   

                                          detail_url    id  \
1  /layers/geonode:S2A_20200810_lat50lon544_T29UQ...  9746   

                                            keywords  \
1  [analysis-ready-data, earth-observation, satel...   

                                            location owner__username  \
1  {u'type': u'Polygon', u'coordinates': [[[-6.17...           admin   

   popular_count  rating                   regions  share_count  \
1              2       0  [Europe, United Kingdom]            0   

   split_granule        srid subtype  \
1            NaN  EPSG:27700  raster   

                            supplemental_information  \
1  Data Collection Time: 11:33:31\nARCSI_CLOUD_CO...   

                                       thumbnail_url  \
1  https://eob-pre1.azure.defra.cloud/uploaded/th...   

                                               title   type  \
1  S2A_20200810_lat50lon544_T29UQR_ORB080_utm29n_...  layer   

                                   uuid  split_granule.cloud_cover  \
1  d0406056-a18c-4e9e-a4aa-404bd20758dc                       17.0   

                                  split_granule.name granule-ref orbit-ref  \
1  geonode:S2A_20200810_lat50lon544_T29UQRSPLIT1_...      T29UQR    ORB080   

     ARCSI_CLOUD_COVER                       title_stub  \
1  0.14184147119522095  S2A_20200810_lat50lon544_T29UQR   

  split_ARCSI_CLOUD_COVER    split_cloud_cover       gran-orb granule-stub  
1       0.173685684800148  0.15776357799768448  T29UQR_ORB080       T29UQR

In [32]:
return_df

abstract  \
0   These data have been created by the Department...   
1   These data have been created by the Department...   
2   These data have been created by the Department...   
3   These data have been created by the Department...   
4   These data have been created by the Department...   
5   These data have been created by the Department...   
6   These data have been created by the Department...   
7   These data have been created by the Department...   
8   These data have been created by the Department...   
9   These data have been created by the Department...   
10  These data have been created by the Department...   
11  These data have been created by the Department...   
12  These data have been created by the Department...   
13  These data have been created by the Department...   
14  These data have been created by the Department...   
15  These data have been created by the Department...   
16  These data have been created by the Department...   
17  These data have been created by the Department...   
18  These data have been created by the Department...   
19  These data have been created by the Department...   
20  These data have been created by the Department...   
21  These data have been created by the Department...   
22  These data have been created by the Department...   
23  These data have been created by the Department...   
24  These data have been created by the Department...   
25  These data have been created by the Department...   
26  These data have been created by the Department...   
27  These data have been created by the Department...   
28  These data have been created by the Department...   
29  These data have been created by the Department...   
30  These data have been created by the Department...   
31  These data have been created by the Department...   
32  These data have been created by the Department...   
33  These data have been created by the Department...   
34  These data have been created by the Department...   
35  These data have been created by the Department...   
36  These data have been created by the Department...   
37  These data have been created by the Department...   
38  These data have been created by the Department...   
39  These data have been created by the Department...   
40  These data have been created by the Department...   
41  These data have been created by the Department...   

                                            alternate  \
0   geonode:S2B_20200805_lat50lon684_T29UPR_ORB080...   
1   geonode:S2A_20200810_lat50lon544_T29UQR_ORB080...   
2   geonode:S2B_20210721_lat51lon538_T29UQS_ORB080...   
3   geonode:S2B_20210718_lat50lon503_T30UUA_ORB037...   
4   geonode:S2B_20210721_lat51lon507_T30UUB_ORB080...   
5   geonode:S2B_20210718_lat50lon363_T30UVA_ORB037...   
6   geonode:S2B_20210718_lat51lon364_T30UVB_ORB037...   
7   geonode:S2B_20210718_lat52lon366_T30UVC_ORB037...   
8   geonode:S2B_20210718_lat53lon367_T30UVD_ORB037...   
9   geonode:S2B_20210721_lat54lon368_T30UVE_ORB080...   
10  geonode:S2B_20210721_lat55lon37_T30UVF_ORB080_...   
11  geonode:S2B_20210721_lat55lon371_T30UVG_ORB080...   
12  geonode:S2B_20190226_lat50lon223_T30UWA_ORB137...   
13  geonode:S2B_20190226_lat51lon222_T30UWB_ORB137...   
14  geonode:S2B_20210718_lat52lon22_T30UWC_ORB037_...   
15  geonode:S2B_20210718_lat53lon219_T30UWD_ORB037...   
16  geonode:S2B_20210718_lat54lon217_T30UWE_ORB037...   
17  geonode:S2A_20210723_lat55lon215_T30UWF_ORB037...   
18  geonode:S2A_20210723_lat55lon213_T30UWG_ORB037...   
19  geonode:S2B_20190226_lat50lon084_T30UXA_ORB137...   
20  geonode:S2B_20190226_lat51lon08_T30UXB_ORB137_...   
21  geonode:S2B_20190226_lat52lon075_T30UXC_ORB137...   
22  geonode:S2B_20190226_lat53lon071_T30UXD_ORB137...   
23  geonode:S2B_20190226_lat54lon066_T30UXE_ORB137...   
24  geonode:S2B_20190226_lat55lon061_T30UXF_ORB137...   
25  geonode:S2A_20200807_lat55lon055_T30UXG_ORB037...   
26  geonode:S2B_20210722_lat50lon056_T30UYA_ORB094... 